#**Getting Started**

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
%cd /content/drive/MyDrive/PumpIt

In [ ]:
!pip install catboost
!pip install category_encoders

In [2]:
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
import seaborn as sns
from sklearn import preprocessing
import datetime as dt
from numpy import mean
from numpy import std

from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.impute import KNNImputer

# encoders
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import OrdinalEncoder
from sklearn.preprocessing import OneHotEncoder
import category_encoders as ce

from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
from sklearn.model_selection import RepeatedStratifiedKFold
from sklearn.model_selection import cross_val_score

# classifiers
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier, StackingClassifier, VotingClassifier, GradientBoostingClassifier
from xgboost.sklearn import XGBClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.neural_network import MLPClassifier
import lightgbm as lgb
from sklearn.linear_model import SGDClassifier
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression
from catboost import CatBoostClassifier
from sklearn import svm

# hyperparameter tuning
from sklearn.model_selection import RandomizedSearchCV, GridSearchCV

from sklearn.decomposition import PCA
from matplotlib.pyplot import figure

#**EDA**

# Importación de los datos
---

In [3]:
features_df = pd.read_csv("training.csv", index_col="id",)
labels_df = pd.read_csv("training_labels.csv", index_col="id")
test_df = pd.read_csv("test.csv", index_col="id")

In [4]:
features_df.head()

amount_tsh date_recorded        funder  gps_height     installer  \
id                                                                        
69572      6000.0    2011-03-14         Roman        1390         Roman   
8776          0.0    2013-03-06       Grumeti        1399       GRUMETI   
34310        25.0    2013-02-25  Lottery Club         686  World vision   
67743         0.0    2013-01-28        Unicef         263        UNICEF   
19728         0.0    2011-07-13   Action In A           0       Artisan   

       longitude   latitude              wpt_name  num_private  \
id                                                               
69572  34.938093  -9.856322                  none            0   
8776   34.698766  -2.147466              Zahanati            0   
34310  37.460664  -3.821329           Kwa Mahundi            0   
67743  38.486161 -11.155298  Zahanati Ya Nanyumbu            0   
19728  31.130847  -1.825359               Shuleni            0   

                         basin  ... payment_type water_quality  quality_group  \
id                              ...                                             
69572               Lake Nyasa  ...     annually          soft           good   
8776             Lake Victoria  ...    never pay          soft           good   
34310                  Pangani  ...   per bucket          soft           good   
67743  Ruvuma / Southern Coast  ...    never pay          soft           good   
19728            Lake Victoria  ...    never pay          soft           good   

           quantity quantity_group                source  \
id                                                         
69572        enough         enough                spring   
8776   insufficient   insufficient  rainwater harvesting   
34310        enough         enough                   dam   
67743           dry            dry           machine dbh   
19728      seasonal       seasonal  rainwater harvesting   

                source_type source_class              waterpoint_type  \
id                                                                      
69572                spring  groundwater           communal standpipe   
8776   rainwater harvesting      surface           communal standpipe   
34310                   dam      surface  communal standpipe multiple   
67743              borehole  groundwater  communal standpipe multiple   
19728  rainwater harvesting      surface           communal standpipe   

      waterpoint_type_group  
id                           
69572    communal standpipe  
8776     communal standpipe  
34310    communal standpipe  
67743    communal standpipe  
19728    communal standpipe  

[5 rows x 39 columns]

In [5]:
X = features_df.copy()
y = labels_df.copy()
X_test = test_df.copy()

In [6]:
X.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 59400 entries, 69572 to 26348
Data columns (total 39 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   amount_tsh             59400 non-null  float64
 1   date_recorded          59400 non-null  object 
 2   funder                 55765 non-null  object 
 3   gps_height             59400 non-null  int64  
 4   installer              55745 non-null  object 
 5   longitude              59400 non-null  float64
 6   latitude               59400 non-null  float64
 7   wpt_name               59400 non-null  object 
 8   num_private            59400 non-null  int64  
 9   basin                  59400 non-null  object 
 10  subvillage             59029 non-null  object 
 11  region                 59400 non-null  object 
 12  region_code            59400 non-null  int64  
 13  district_code          59400 non-null  int64  
 14  lga                    59400 non-null  object 
 15

Combino los los datos del train y del test

In [7]:
df=X.append(X_test)

C:\Users\Kim\AppData\Local\Temp\ipykernel_8620\2612045130.py:1: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df=X.append(X_test)


In [8]:
df.describe()

amount_tsh    gps_height     longitude      latitude   num_private  \
count   74250.000000  74250.000000  74250.000000  7.425000e+04  74250.000000   
mean      318.685704    665.667313     34.074262 -5.701771e+00      0.462330   
std      2906.762364    692.761033      6.572519  2.944969e+00     11.537879   
min         0.000000    -90.000000      0.000000 -1.164944e+01      0.000000   
25%         0.000000      0.000000     33.086819 -8.525675e+00      0.000000   
50%         0.000000    364.000000     34.907475 -5.026540e+00      0.000000   
75%        20.000000   1317.000000     37.181685 -3.325058e+00      0.000000   
max    350000.000000   2777.000000     40.345193 -2.000000e-08   1776.000000   

        region_code  district_code    population  construction_year  
count  74250.000000   74250.000000  74250.000000       74250.000000  
mean      15.265414       5.629077    180.750828        1298.463650  
std       17.508907       9.641636    471.086120         952.349375  
min        1.000000       0.000000      0.000000           0.000000  
25%        5.000000       2.000000      0.000000           0.000000  
50%       12.000000       3.000000     25.000000        1986.000000  
75%       17.000000       5.000000    215.000000        2004.000000  
max       99.000000      80.000000  30500.000000        2013.000000

In [9]:
y.head()

status_group
id                   
69572      functional
8776       functional
34310      functional
67743  non functional
19728      functional

# Reporte descriptivo 

In [10]:
import pandas_profiling
pandas_profiling.ProfileReport(df)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Limpieza de datos

In [12]:
X_null = X.isnull().sum()
print(X_null)

amount_tsh                   0
date_recorded                0
funder                    3635
gps_height                   0
installer                 3655
longitude                    0
latitude                     0
wpt_name                     0
num_private                  0
basin                        0
subvillage                 371
region                       0
region_code                  0
district_code                0
lga                          0
ward                         0
population                   0
public_meeting            3334
recorded_by                  0
scheme_management         3877
scheme_name              28166
permit                    3056
construction_year            0
extraction_type              0
extraction_type_group        0
extraction_type_class        0
management                   0
management_group             0
payment                      0
payment_type                 0
water_quality                0
quality_group                0
quantity

In [13]:
test_null = X_test.isnull().sum()
print(test_null)

amount_tsh                  0
date_recorded               0
funder                    869
gps_height                  0
installer                 877
longitude                   0
latitude                    0
wpt_name                    0
num_private                 0
basin                       0
subvillage                 99
region                      0
region_code                 0
district_code               0
lga                         0
ward                        0
population                  0
public_meeting            821
recorded_by                 0
scheme_management         969
scheme_name              7092
permit                    737
construction_year           0
extraction_type             0
extraction_type_group       0
extraction_type_class       0
management                  0
management_group            0
payment                     0
payment_type                0
water_quality               0
quality_group               0
quantity                    0
quantity_g

In [15]:
list_features = X_test.columns
print('Number of features : ',len(list_features))
print('')
i = 0
for f in list_features:
    print('feature:', f, '|| Type:', type(X[f][0]), '|| Example:', X[f][0], '|| number of unique values', len(X[f].unique()), '|| missing values training : ', (X_null.values[i]/X.shape[0])*100, '|| missing values test : ', (test_null.values[i]/X_test.shape[0])*100 )
    i +=1

Number of features :  39

feature: amount_tsh || Type: <class 'numpy.float64'> || Example: 0.0 || number of unique values 98 || missing values training :  0.0 || missing values test :  0.0
feature: date_recorded || Type: <class 'str'> || Example: 2012-11-13 || number of unique values 356 || missing values training :  0.0 || missing values test :  0.0
feature: funder || Type: <class 'str'> || Example: Tasaf || number of unique values 1898 || missing values training :  6.11952861952862 || missing values test :  5.851851851851852
feature: gps_height || Type: <class 'numpy.int64'> || Example: 0 || number of unique values 2428 || missing values training :  0.0 || missing values test :  0.0
feature: installer || Type: <class 'str'> || Example: TASAF || number of unique values 2146 || missing values training :  6.153198653198653 || missing values test :  5.905723905723906
feature: longitude || Type: <class 'numpy.float64'> || Example: 33.1258283 || number of unique values 57516 || missing val

In [16]:
#finding Zero Percentage in each column
all = X.shape[0]
X_zero = X.astype(bool).sum(axis=0)
list_X = X_test.columns
print('Number of features : ',len(list_X))
print('')
i = 0
for f in list_X:
  if (((all - X_zero.values[i])/all)*100 > 0):
    print('feature:', f, '|| Type:', type(X[f][0]),'|| Example:', X[f][0], '|| zero percentage', ((all - X_zero.values[i])/all)*100 )
  i += 1

Number of features :  39

feature: amount_tsh || Type: <class 'numpy.float64'> || Example: 0.0 || zero percentage 70.09932659932659
feature: gps_height || Type: <class 'numpy.int64'> || Example: 0 || zero percentage 34.40740740740741
feature: longitude || Type: <class 'numpy.float64'> || Example: 33.1258283 || zero percentage 3.05050505050505
feature: num_private || Type: <class 'numpy.int64'> || Example: 0 || zero percentage 98.72558922558923
feature: district_code || Type: <class 'numpy.int64'> || Example: 3 || zero percentage 0.038720538720538725
feature: population || Type: <class 'numpy.int64'> || Example: 0 || zero percentage 35.994949494949495
feature: public_meeting || Type: <class 'float'> || Example: nan || zero percentage 8.51010101010101
feature: permit || Type: <class 'bool'> || Example: True || zero percentage 29.44781144781145
feature: construction_year || Type: <class 'numpy.int64'> || Example: 0 || zero percentage 34.86363636363636


In [17]:
#remove columns with zeros and more missing values along with more unique values
df.drop(columns=['num_private', 'scheme_name'], axis=1, inplace=True)

In [18]:
#drop unwanted columns
df.drop(columns=['amount_tsh','recorded_by','wpt_name'], axis=1, inplace=True)

**Handling Missing Values**

In [19]:
# Number of missing values in each column
missing_val_count_by_column = (df.isnull().sum())
print(missing_val_count_by_column[missing_val_count_by_column > 0])

funder               4504
installer            4532
subvillage            470
public_meeting       4155
scheme_management    4846
permit               3793
dtype: int64


*   num_private - droped - only one unique value
*   wpt_name - droped - number of unique values 37400
*   num_private, scheme_name - droped
*   Population - need to search more 36% zero count - relaced zeros with nan and mean
*   funder - mode
*   installer - mode
*   subvilage - mode
*   public_meeting - mode
*   scheme_management - mode
*   permit - mode
*   construction year - replace zeros with nan and use mode









In [20]:
mis_columns = ['construction_year','population']
for col in mis_columns:
  df[col].replace(0, np.nan, inplace=True)

In [21]:
# Fill missing values with mode
def fill_mode(all_column,X):
  for X_column in all_column:
    X[X_column] = X[X_column].fillna(X[X_column].mode()[0])
  return X

In [22]:
df = fill_mode(["funder","installer","subvillage","public_meeting","scheme_management","permit","construction_year"],df)

In [23]:
# Fill missing values with mean
def fill_mean(all_column,X):
  for X_column in all_column:
    X[X_column] = X[X_column].fillna(round(X[X_column].mean()))
  return X

In [24]:
df = fill_mean(["population"],df)

In [25]:
# Number of missing values in each column
missing_val_count_by_column = (df.isnull().sum())
print(missing_val_count_by_column[missing_val_count_by_column > 0])

Series([], dtype: int64)


*   *No missing values*

#**Data Preprocessing**

In [26]:
#date time
df.date_recorded = pd.to_datetime(df.date_recorded)

In [27]:
df['year'] = df['date_recorded'].dt.year
df['month'] = df['date_recorded'].dt.month
df['day_of_months'] = df['date_recorded'].dt.day

In [28]:
df.drop(columns=['date_recorded'], axis=1, inplace=True)

In [29]:
#Payment
df["Payment_all"] = df["payment"] + df["payment_type"]

#quality
df["Quality_all"] = df["water_quality"] + df["quality_group"]

#Quantitiy
df["Quantity_all"] = df["quantity"] + df["quantity_group"]

#waterpoint_type
df["Waterpoint_all"] = df["waterpoint_type"] + df["waterpoint_type_group"]

In [30]:
#drop unwanted columns
df.drop(columns=['payment','payment_type','water_quality','quality_group','quantity','quantity_group','waterpoint_type','waterpoint_type_group'], axis=1, inplace=True)

**Encoding**

In [31]:
#one hot encoding
def one_hot_encode(df,object_cols):
  OH_encoder = OneHotEncoder(handle_unknown='ignore', sparse=False)
  OH_cols_train = pd.DataFrame(OH_encoder.fit_transform(df[object_cols]))

  # One-hot encoding removed index; put it back
  OH_cols_train.index = df.index

  # Remove categorical columns (will replace with one-hot encoding)
  num_X_train = df.drop(object_cols, axis=1)

  # Add one-hot encoded columns to numerical features
  df = pd.concat([num_X_train, OH_cols_train], axis=1)
  return df

In [32]:
columns=['source','source_type','source_class','public_meeting','permit','extraction_type','extraction_type_group','extraction_type_class','management','management_group',"basin", "scheme_management","Payment_all","Quality_all","Quantity_all","Waterpoint_all"]
df = one_hot_encode(df, columns)
# one_hot_encode(test, columns)

C:\Users\Kim\anaconda3\lib\site-packages\sklearn\preprocessing\_encoders.py:828: FutureWarning: `sparse` was renamed to `sparse_output` in version 1.2 and will be removed in 1.4. `sparse_output` is ignored unless you leave `sparse` to its default value.
  warnings.warn(


In [33]:
#binary encoder
#use if count of unique values is more than 15
 
enc = ce.BinaryEncoder(cols=['funder','installer', 'subvillage', 'region','lga','ward']).fit(df)
df = enc.transform(df)

#**Separate training and test set**

In [34]:
X = df[:len(features_df)]
X_test = df[len(features_df):]

In [35]:
X.head()

funder_0  funder_1  funder_2  funder_3  funder_4  funder_5  funder_6  \
id                                                                            
69572         0         0         0         0         0         0         0   
8776          0         0         0         0         0         0         0   
34310         0         0         0         0         0         0         0   
67743         0         0         0         0         0         0         0   
19728         0         0         0         0         0         0         0   

       funder_7  funder_8  funder_9  ...  117  118  119  120  121  122  123  \
id                                   ...                                      
69572         0         0         0  ...  0.0  0.0  0.0  0.0  0.0  1.0  0.0   
8776          0         0         0  ...  1.0  0.0  0.0  0.0  0.0  1.0  0.0   
34310         0         0         0  ...  0.0  0.0  0.0  0.0  1.0  0.0  0.0   
67743         0         0         1  ...  0.0  0.0  0.0  0.0  1.0  0.0  0.0   
19728         0         0         1  ...  0.0  1.0  0.0  0.0  0.0  1.0  0.0   

       124  125  126  
id                    
69572  0.0  0.0  0.0  
8776   0.0  0.0  0.0  
34310  0.0  0.0  0.0  
67743  0.0  0.0  0.0  
19728  0.0  0.0  0.0  

[5 rows x 200 columns]

In [36]:
X_test.head()

funder_0  funder_1  funder_2  funder_3  funder_4  funder_5  funder_6  \
id                                                                            
50785         0         0         0         0         1         0         1   
51630         0         0         0         0         0         0         0   
17168         0         0         0         0         0         0         0   
45559         0         0         0         0         1         0         0   
49871         0         1         0         0         0         0         0   

       funder_7  funder_8  funder_9  ...  117  118  119  120  121  122  123  \
id                                   ...                                      
50785         0         0         0  ...  0.0  1.0  0.0  0.0  0.0  0.0  0.0   
51630         1         0         1  ...  1.0  0.0  0.0  0.0  0.0  1.0  0.0   
17168         1         0         1  ...  1.0  0.0  0.0  0.0  0.0  0.0  0.0   
45559         1         0         0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
49871         0         1         1  ...  0.0  0.0  0.0  0.0  0.0  1.0  0.0   

       124  125  126  
id                    
50785  0.0  0.0  1.0  
51630  0.0  0.0  0.0  
17168  0.0  0.0  1.0  
45559  0.0  0.0  1.0  
49871  0.0  0.0  0.0  

[5 rows x 200 columns]

In [37]:
X.shape

(59400, 200)

In [38]:
X_test.shape

(14850, 200)

#**Model Training**

In [39]:
def score_dataset(X, y, model):
    cv = RepeatedStratifiedKFold(n_splits=10, n_repeats=3, random_state=0)
    # Metric is Accuracy
    score = cross_val_score(
        model, X, y, scoring='accuracy', cv=cv, n_jobs=-1, error_score='raise')
    print('Accuracy: %.3f (%.3f)' % (mean(score), std(score)))

In [40]:
modelRF = RandomForestClassifier(n_estimators=400, random_state=0,max_depth=20)
modelETC = ExtraTreesClassifier(n_estimators=1000,min_samples_split=10)
modelXGB = XGBClassifier()
modelCAT = CatBoostClassifier(max_ctr_complexity=5, task_type='CPU', iterations=1000,
                   eval_metric='AUC', od_type='Iter', od_wait=500, loss_function = 'MultiClass', random_seed=1, depth=10, learning_rate = 0.03, l2_leaf_reg = 1)
modelMLP = MLPClassifier()
modelSVM = SVC(kernel='linear', C=1,gamma='auto')

In [41]:
# score model
scoreSVM = score_dataset(X,y,modelSVM)

TypeError: Feature names are only supported if all input features have string names, but your input has ['int', 'str'] as feature name / column name types. If you want feature names to be stored and validated, you must convert them all to strings, by using X.columns = X.columns.astype(str) for example. Otherwise you can remove feature / column names from your input data, or convert them all to a non-string data type.

In [42]:
# score model
scoreRFTest = score_dataset(X,y,modelRF)

TypeError: Feature names are only supported if all input features have string names, but your input has ['int', 'str'] as feature name / column name types. If you want feature names to be stored and validated, you must convert them all to strings, by using X.columns = X.columns.astype(str) for example. Otherwise you can remove feature / column names from your input data, or convert them all to a non-string data type.

In [43]:
# score model
scoreXGB = score_dataset(X,y,modelXGB)

ValueError: Invalid classes inferred from unique values of `y`.  Expected: [0 1 2], got ['functional' 'functional needs repair' 'non functional']

In [ ]:
# score model
scoreETC = score_dataset(X,y,modelETC)

#**Hyperparameter Tunning**

In [ ]:
def grid_search(model, params, X_tune, y_tune):
  clf =  GridSearchCV(model, params, cv=5, scoring='accuracy')
  clf.fit(X_tune, y_tune)
  return clf.best_score_, clf.best_params_

In [ ]:
model_params = {
    'random_forest': {
        'model': RandomForestClassifier(),
        'params' : {
            'n_estimators': [50,100,200,400],
            'max_depth': [5, 10, 20, 100]
        }
    },
    'xg_boost': {
        'model': XGBClassifier(),
        'params' : {
            'eta': [0.01, 0.1, 0.2, 0.4],
            'max_depth': [5, 10, 15, 20, 22, 100]
        }
    },
    'cat_boost': {
        'model': CatBoostClassifier(loss_function = 'MultiClass', iterations=1000),
        'params' : {
            'learning_rate': [0.03, 0.1],
            'depth':[4, 6, 10],
            'l2_leaf_reg': [1, 3, 5, 7, 9]
        }
    }
}

In [ ]:
X_tune=X
y_tune = y.status_group

In [ ]:
best_score, best_params = grid_search(model_params['random_forest']['model'], model_params['random_forest']['params'], X_tune, y_tune)
print(best_score, best_params)

In [ ]:
best_score, best_params = grid_search(model_params['xg_boost']['model'], model_params['xg_boost']['params'], X_tune, y_tune)
print(best_score, best_params)

In [ ]:
best_score, best_params = grid_search(model_params['cat_boost']['model'], model_params['cat_boost']['params'], X_tune, y_tune)
print(best_score, best_params)

#**Ensembling**

In [ ]:
estimators_stacked = [
              #('xbg', modelXGB),
              # ('mlp', modelMLP),
              #('cat',modelCAT),
              ('xt', modelETC),
              ('rn', modelRF)
             ]

# Stacking Classifier
stacked_estimator =  StackingClassifier(estimators=estimators_stacked,
                                    final_estimator=LogisticRegression()  
                                  )
# Voting Classifier
voting_estimator = VotingClassifier(estimators=estimators_stacked, 
                        voting='hard')  # hard if labels needed, soft if probabilites needed

In [ ]:
# score model
scoreEns = score_dataset(X,y,stacked_estimator)

#**Train on entire dataset**

In [ ]:
model = modelRF
X_train = X
y_train = y

model.fit(X_train, y_train)

In [ ]:
#ETC,RF
modelEns = stacked_estimator
X_train = X
y_train = y

modelEns.fit(X_train, y_train)

In [ ]:
#ETC,RF,cat
modelEns = stacked_estimator
X_train = X
y_train = y

modelEns.fit(X_train, y_train)

#**Predict**

In [ ]:
predict=model.predict(X_test)

In [ ]:
predict=modelEns.predict(X_test)

#**Submission**

In [ ]:
submission_df = pd.read_csv("SubmissionFormat.csv", 
                            index_col="id")

In [ ]:
# Make sure we have the rows in the same order
np.testing.assert_array_equal(test_df.index.values, 
                              submission_df.index.values)

# Save predictions to submission data frame
submission_df["status_group"] = predict

In [ ]:
submission_df.to_csv('my_submission.csv', index=True)

In [ ]:
from google.colab import files
files.download('my_submission.csv')